In [2]:
from huggingface_hub import notebook_login
notebook_login()


In [1]:
!pip install unsloth

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.8/57.8 kB 3.3 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of torchvision to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 188.7/188.7 kB 8.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 484.9/484.9 kB 27.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 162.1/162.1 kB 13.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 55.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 43.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 30.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56

In [3]:
from unsloth import FastLanguageModel
import torch
from transformers import AutoModelForSequenceClassification, AutoTokenizer, TrainingArguments, Trainer
from datasets import Dataset, DatasetDict
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, precision_recall_fscore_support

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.
🦥 Unsloth Zoo will now patch everything to make training faster!


In [4]:
df = pd.read_csv("Telugu.csv")  # Replace "your_dataset.csv" with your filename
df = df.dropna() # remove null values
df = df.rename(columns={"text_column": "text", "label_column": "label"}) # rename colums
print(df.head())  # Inspect the first few rows

             en                       te
0   Wonderful!.                అద్భుతం!.
1  Definitely!.               తప్పకుండా.
2   He hung up.          అతను పెట్టేసాడు
3   I ran home.  నేను ఇంటికి పరిగెత్తాను
4  Who are we?.            మేము ఎవరము ?.


In [8]:
from google.colab import drive

try:
  drive.flush_and_unmount()
  print('Drive unmounted')
except ValueError:
  pass

# Remount the drive
drive.mount('/content/drive')
df = pd.read_csv("/content/Telugu.csv") # replace with your path in Google Drive
df = df.dropna() # remove null values
df = df.rename(columns={"text_column": "text", "label_column": "label"}) # rename colums
print(df.head())

Drive unmounted
Mounted at /content/drive
             en                       te
0   Wonderful!.                అద్భుతం!.
1  Definitely!.               తప్పకుండా.
2   He hung up.          అతను పెట్టేసాడు
3   I ran home.  నేను ఇంటికి పరిగెత్తాను
4  Who are we?.            మేము ఎవరము ?.


In [41]:
dataset = Dataset.from_pandas(df)

In [42]:
dataset = dataset.train_test_split(test_size=0.2, seed=42)  # 80% train, 20% validation.  seed for reproducibility

In [45]:
model_name = "bert-base-multilingual-cased"  # Or try "xlm-roberta-base" if that's faster
tokenizer = AutoTokenizer.from_pretrained(model_name)

In [15]:
def tokenized_function(examples):
  tokenized_datasets = dataset.map(preprocess_function, batched=True)
  return tokenized_datasets

def tokenize_fn(examples):
    inputs = [ex for ex in examples['te']]
    targets = [ex for ex in examples['en']]
    model_inputs = tokenizer(inputs, max_length=128, truncation=True, padding="max_length")
    labels = tokenizer(targets, max_length=128, truncation=True, padding="max_length").input_ids
    model_inputs["labels"] = labels
    return model_inputs

tokenized_dataset = dataset.map(tokenize_fn, batched=True)

Map:   0%|          | 0/336536 [00:00<?, ? examples/s]

Map:   0%|          | 0/84135 [00:00<?, ? examples/s]

In [16]:
def compute_metrics(pred):
    labels = pred.label_ids
    preds = pred.predictions.argmax(-1)
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='binary')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall
    }

In [17]:
model = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)

model.safetensors:   0%|          | 0.00/714M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-multilingual-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [19]:
!pip install peft
from peft import LoraConfig, get_peft_model

# ... (rest of your code)

lora_config = LoraConfig(
    r=16,
    lora_alpha=32,
    target_modules=["query", "key", "value", "dense"],
    lora_dropout=0.05,
    bias="none",
    task_type="SEQ_CLS", # Specify task type as sequence classification
)

model = get_peft_model(model, lora_config) # Use peft.get_peft_model directly

In [25]:
from peft import LoraConfig, get_peft_model

# ... (rest of your code)

lora_config = LoraConfig(
    r=16,
    lora_alpha=32,
    target_modules=["query", "key", "value", "dense"],
    lora_dropout=0.05,
    bias="none",
    task_type="SEQ_CLS",  # Specify task type as sequence classification
)

model = get_peft_model(model, lora_config)  # Use peft.get_peft_model directly

In [26]:
training_args = TrainingArguments(
    output_dir="./results",
    learning_rate=2e-5,
    per_device_train_batch_size=32,
    per_device_eval_batch_size=32,
    num_train_epochs=3,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
    metric_for_best_model="f1", # Use F1 score to determine the best model
    report_to="none" # Disable WANDB to avoid login issues
)

/usr/local/lib/python3.11/dist-packages/transformers/training_args.py:1575: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [55]:
tokenized_datasets = dataset.map(tokenize_fn, batched=True)
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["test"],
    tokenizer=tokenizer,
    compute_metrics=compute_metrics,
)

Map:   0%|          | 0/336536 [00:00<?, ? examples/s]

Map:   0%|          | 0/84135 [00:00<?, ? examples/s]

<ipython-input-55-cbba859dcebd>:2: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [56]:
trainer.save_model("./my_colloquial_telugu_model")

In [57]:
from huggingface_hub import notebook_login

notebook_login()

In [60]:
import os

# Replace "YOUR_HUGGING_FACE_TOKEN" with the actual token you copied
os.environ["ML_project_token"] = "ML_project_token"